# 5.7. Kaggle House Prices – MLP

In [34]:
%matplotlib inline

import sys
sys.path.append("../..")

import pandas as pd
import torch

from dataloaders import KaggleHouse
from models import DropoutMLPRegression
from utils import Trainer

In [35]:
data = KaggleHouse(batch_size=64)
data.preprocess()
data.train.shape

(1460, 331)

### k-Fold Cross-Validation

In [36]:
hparams = {'num_outputs':1, 'num_hiddens_1':512, 'num_hiddens_2':512,
           'dropout_1':0.05, 'dropout_2':0.05, 'lr':0.001}

In [37]:
def k_fold_data(data, k):
    rets = []
    fold_size = data.train.shape[0] // k
    for j in range(k):
        idx = range(j * fold_size, (j+1) * fold_size)
        rets.append(KaggleHouse(data.batch_size, data.train.drop(index=idx),
                                data.train.loc[idx]))
    return rets

In [ ]:
def k_fold(trainer, data, k, lr):
    val_loss, models = [], []
    #models.append(1)
    for i, data_fold in enumerate(k_fold_data(data, k)):
        model = DropoutMLPRegression(**hparams)
        model.board.yscale='log'
        if i != 0: model.board.display = False
        trainer.fit(model, data_fold)
        val_loss.append(float(model.board.data['val_loss'][-1].y))
        #models[0] = model
        models.append(model)
    print(f'average validation log mse = {sum(val_loss)/len(val_loss)}')
    return models

### Training

In [41]:
trainer = Trainer(max_epochs=200)
models = k_fold(trainer, data, k=5, lr=0.001)

average validation log mse = 0.05637814477086067


### Submitting Predictions on Kaggle

In [40]:
preds = [model(torch.tensor(data.val.values.astype(float), dtype=torch.float32))
         for model in models]
# Taking exponentiation of predictions in the logarithm scale
ensemble_preds = torch.exp(torch.cat(preds, 1)).mean(1)
submission = pd.DataFrame({'Id':data.raw_val.Id,
                           'SalePrice':ensemble_preds.detach().numpy()})
submission.to_csv('submission.csv', index=False)